# Iron Population Clustering

In data science, a domain defines the type of data value that is held by an attribute in a data model. For the Rocklea dome case we want to define domains in which samples would have a similar iron concentration. It can be two different domains for instance, one with a high iron concentration and the other one with a low iron concentration.

## Different types of domain

Different domains are defined by the way they are created. hose created through classical clustering show poor spatial contiguity compared to ones obtained by geostatistical clustering. Classical clustering does not include spatial information and tends to produce spatially scattered groups of samples which is a problem in mining exploitation whereas geostatistical clustering allows to have spacially contiguous clusters. This method allows to have better domains in mining exploration but is more complicated to use. An alternative approach consists in using classical clustering methods on spacially contiguous data set.

To visualize the different domains we can represent them through histograms.

## Histograms

A histogram is an approximate representation of the distribution of numerical data. To construct a histogram the first step is to divide the entire range of values into a series of intervals and then count how many values fall into each interval. The vertical y-axis represents the number count or percentage of occurences in the data for each column.

First we need to import the useful libraries and csv files.

In [ ]:
import geolime as geo
from pyproj import CRS
import numpy as np
from sklearn.cluster import KMeans
import pyvista as pv

pv.set_jupyter_backend('panel')


geo.Project().set_crs(CRS("EPSG:20350"))

In [ ]:
dh = geo.read_file("../data/domained_drillholes.geo")

In [ ]:
dh.user_properties()

To determine the number of domains that we need we can look at the geology of the Rocklea dome area. The biggest part of the iron deposits have been made during the same era and form a layer of alternating shales. As this formation is the only one exploited for iron mining we can create two domains, one rich in iron and one poor in iron where the limit will be this iron rich formation.
There is also a paleochannel very rich in iron but it takes its source in the precedent rich iron deposit so we can assume they both belongs to the same domain.

To create these two domains we can have a first look at the ferric distribution in the area.

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct"}], nbins=20)

This histogram shows a bivariate distribution of the iron concentration in the area. The first peak corresponds to a low iron concentration and the second one to a high iron concentration. The separation between these two domains seems to be around 30 %. 
If we look at the two domains created we have :

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "Fe_pct <= 30"},
        {"object": dh, "property": "Fe_pct", "region": "Fe_pct >= 30"}
    ],
    nbins=30
)

In [ ]:
dh.data("Fe_pct", region="Fe_pct >= 30")

As we can see we have two separate domains but we want to make a more accurate separation. For this we can use the chemical and mineralogical correlation study. We will consider four correlations : the positives correlations with the ferric oxides abundance and the kaolin abundance and the negative correlations with the silica and alumina.

## Correlation between "Fe %" and "SiO2 %"

This is the highest negative correlation, -0.9. A high concentration in silica implies a low concentration in iron. We can separate the domains according to the silica concentration but first we need to find the most accurate silica treshold where we will clearly have a domain with a high silica concentration and one with a low silica concentration.

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "SiO2_pct"}], nbins=20)

We see a big landing around 30. We can try different separation treshold to find the more accurate. To study the accuracy we can calculate the variance of the list of values. The smallest the variance is the better is the separation of the domains.

In [ ]:
dh.data("Fe_pct", region="SiO2_pct < 30").var()

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"SiO2_pct < 30"}], nbins=30)

In [ ]:
dh.data("Fe_pct", region="SiO2_pct < 25").var()

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"SiO2_pct < 25"}], nbins=30)

We can choose 25 % for the silica treshold. Now let's look at the complementary domain.

In [ ]:
dh.data("Fe_pct", region="SiO2_pct > 25").var()

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"SiO2_pct > 25"}], nbins=10)

We have two univariate domains.

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "SiO2_pct < 25"},
        {"object": dh, "property": "Fe_pct", "region": "SiO2_pct > 25"}
    ],
    nbins=10
)

Finally, the precedent histogram shows the two different domains created with the SiO2 % parameters. We can do the same with the three other chemical and mineralogical data.

## Correlation between "Fe %" and "Fe ox ai"

The correlaation coefficient between these two elements is 0.8. A high abundance in ferric oxides implies a high concentration in iron.

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_ox_ai"}], nbins=10)

We can put separation around 0.20.

In [ ]:
np.nanvar(dh.data("Fe_pct", region="Fe_ox_ai < 0.2"))

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"Fe_ox_ai < 0.2"}], nbins=10)

In [ ]:
np.nanvar(dh.data("Fe_pct", region="Fe_ox_ai > 0.2"))

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"Fe_ox_ai > 0.2"}], nbins=10)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "Fe_ox_ai > 0.2"},
        {"object": dh, "property": "Fe_pct", "region": "Fe_ox_ai < 0.2"}
    ],
    nbins=10
)

## Correlation between "Fe %" and "kaolin abundance"

The correlation coefficient between these two elements is -0.8. A high abundance in kaolin implies a low concentration in iron.

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "kaolin_abundance"}], nbins=20)

We can look for a separation around 0.10.

In [ ]:
np.nanvar(dh.data("Fe_pct", region="kaolin_abundance > 0.1"))

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"kaolin_abundance > 0.1"}], nbins=10)

In [ ]:
np.nanvar(dh.data("Fe_pct", region="kaolin_abundance < 0.1"))

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Fe_pct", "region":"kaolin_abundance < 0.1"}], nbins=10)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance > 0.1"},
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance < 0.1"}
    ],
    nbins=10
)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance > 0.12"},
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance < 0.12"}
    ],
    nbins=10
)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance > 0.09"},
        {"object": dh, "property": "Fe_pct", "region": "kaolin_abundance < 0.09"}
    ],
    nbins=10
)

## Correlation between "Fe %" and "Al2O3"

The correlation coefficient between these two elements is -0.7.

In [ ]:
geo.histogram_plot(data=[{"object": dh, "property": "Al2O3"}], nbins=20)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 > 8"},
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 < 8"}
    ],
    nbins=20
)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 > 10"},
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 < 10"}
    ],
    nbins=10
)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 > 14"},
        {"object": dh, "property": "Fe_pct", "region": "Al2O3 < 14"}
    ],
    nbins=10
)

Now that we studied all the correlations we can use them together to create more accurate domains.

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "(SiO2_pct < 25) & (Fe_ox_ai > 0.2)"},
        {"object": dh, "property": "Fe_pct", "region": "(SiO2_pct > 25) & (Fe_ox_ai < 0.2)"}
    ],
    nbins=10
)

Silica and ferric oxide abundance already gave two great domains. We can also try to add the two other correlations.

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "(SiO2_pct < 25) & (Fe_ox_ai > 0.2) & (kaolin_abundance < 0.09) & (Al2O3 < 14)"},
        {"object": dh, "property": "Fe_pct", "region": "(SiO2_pct > 25) & (Fe_ox_ai < 0.2) & (kaolin_abundance > 0.09) & (Al2O3 > 14)"}
    ],
    nbins=10
)

We can look at the variance of the different domains for the first and the last histogram to see if we have something more accurate thanks to the correlations.

For the domains created with the iron percentage we have :

In [ ]:
dh.data("Fe_pct", region="Fe_pct < 30").var()

In [ ]:
dh.data("Fe_pct", region="Fe_pct > 30").var()

And for those created with the correlation relation we have :

In [ ]:
dh.data("Fe_pct", region="(SiO2_pct < 25) & (Fe_ox_ai > 0.2) & (kaolin_abundance < 0.09) & (Al2O3 < 14)").var()

In [ ]:
dh.data("Fe_pct", region="(SiO2_pct > 25) & (Fe_ox_ai < 0.2) & (kaolin_abundance > 0.09) & (Al2O3 > 14)").var()

In [ ]:
dh.set_property_expr(name="manual_classif_code", expr="sqrt(-1)")
dh.set_property_expr(name="manual_classif_code", expr="1", region="((SiO2_pct < 28) & (Fe_ox_ai > 0.15) & (Fe_pct > 25) & (Al2O3 < 14))")
dh.set_property_expr(name="manual_classif_code", expr="0", region="((SiO2_pct >= 28) | (Fe_ox_ai <= 0.15) | (Fe_pct <= 25) | (Al2O3 >= 14))")

In [ ]:
dh.set_property_expr(name="manual_classif", expr="sqrt(-1)")
dh.set_property_expr(name="manual_classif", expr="'LowGrade'", region="manual_classif_code == 0")
dh.set_property_expr(name="manual_classif", expr="'HighGrade'", region="manual_classif_code == 1")

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "manual_classif == 'LowGrade'"},
        {"object": dh, "property": "Fe_pct", "region": "manual_classif == 'HighGrade'"}
    ],
    nbins=10
)

We can notice that for both domains the variance is lower with the correlation separation, which means that these are more accurate and better for mining exploitation.

## What about automatic domaining ? 

In [ ]:
X = dh.data(["Fe_ox_ai", "SiO2_pct", "Al2O3", "Fe_pct"], "Fe_ox_ai + SiO2_pct + Al2O3 + Fe_pct > 0")

In [ ]:
kmeans = KMeans(n_clusters=2).fit(X)

In [ ]:
dh.set_property_expr(name="sk_classif_code", expr="sqrt(-1)")

In [ ]:
dh.set_property_value(name="sk_classif_code", data=kmeans.labels_, region="Fe_ox_ai + SiO2_pct + Al2O3 + Fe_pct > 0")

In [ ]:
dh.set_property_expr(name="sk_classif", expr="sqrt(-1)")
dh.set_property_expr(name="sk_classif", expr="'LowGrade'", region="sk_classif_code == 0")
dh.set_property_expr(name="sk_classif", expr="'HighGrade'", region="sk_classif_code == 1")

In [ ]:
np.unique(kmeans.labels_)

In [ ]:
geo.histogram_plot(
    data=[
        {"object": dh, "property": "Fe_pct", "region": "sk_classif == 'LowGrade'"},
        {"object": dh, "property": "Fe_pct", "region": "sk_classif == 'HighGrade'"}
    ],
    nbins=10
)

In [ ]:
dh.data("Fe_pct", region="sk_classif == 'LowGrade'").var()

In [ ]:
dh.data("Fe_pct", region="sk_classif == 'HighGrade'").var()

In [ ]:
dh.to_file("../data/dh_pop_classif")

## Comparison with Geometric Modelling

In [ ]:
gs = geo.read_file("../data/surfaces.geo")

In [ ]:
gs_pv_low = gs.to_pyvista('hard_top_Lower')
gs_pv_up = gs.to_pyvista('hard_top_Upper')
gs_pv_ore = gs.to_pyvista('hard_top_OreZone')
dh_pv = dh.to_pyvista('domain_code')

In [ ]:
domain_solid = geo.datasets.load("rocklea_dome/domain_mesh.dxf")
domain_solid_pv = domain_solid.to_pyvista()

In [ ]:
p = pv.Plotter()

p.add_mesh(gs_pv_low, color='r')
p.add_mesh(domain_solid_pv, color='y')

p.add_mesh(dh_pv.tube(radius=20))

p.set_scale(zscale=20)

p.show()